In [1]:
def discrete_forrier_transform(N, fs, signal):
    
    #Initial Array
    X_real = np.zeros(10000)
    X_imj = np.zeros(10000)
    MagDFT = np.zeros(10000)

    #DFT
    for k in range (N):
        for n in range (N):
            X_real[k] += (signal[n])*np.cos(2*np.pi*k*n/N)
            X_imj[k] -= (signal[n])*np.sin(2*np.pi*k*n/N)

    for k in range (N):
        MagDFT[k] = np.sqrt(np.square(X_real[k])+np.square(X_imj[k]))
    return MagDFT

In [2]:
import numpy
import csv
import matplotlib.pyplot as plt 
import plotly.graph_objects as go
import pandas
import numpy as np

In [3]:
time = []
signal = []

with open('data.txt') as file:
    lines = csv.reader(file, delimiter='\t')
    for row in lines:
        values = row[0].split()
        if len(values) == 2:
            time_value = int(values[0])
            signal_value = float(values[1])
            time.append(time_value)
            signal.append(signal_value-1.25)


fig = go.Figure(data=go.Scatter(x=time, y=signal, mode='lines'))
fig.update_layout(
    title="Original Signal",
    xaxis_title="Sequence (n)",
    yaxis_title="Amplitude (mV)",
    width=800,
    height=500,
    xaxis=dict(showline=True, showgrid=True),
    yaxis=dict(showline=True, showgrid=True)
)
fig.show()


In [4]:
N = len(signal)
fs = 1000 

MagDFT_full = discrete_forrier_transform(N, fs, signal)
k =  np.arange (0, N, 1, dtype=int)
n = np.arange (0, N, 1, dtype=int)
#Plotting 
fig_DFT = go.Figure(data=go.Scatter(x=k*fs/N, y=MagDFT_full[k], mode='markers + lines'))
fig_DFT.update_layout(
    title="DFT Signal",
    xaxis_title="Frequency (Hz)",
    yaxis_title="Magnitude)",
    width=800,
    height=500,
    xaxis=dict(showline=True, showgrid=True),
    yaxis=dict(showline=True, showgrid=True)
)
fig_DFT.show()


In [5]:
#Preprocessing Signal with MAV 

import numpy as np

def movingAverage(signal, window):
    sum = 0
    mAver_forward = []
    mAver_backward = []
    k = int((window - 1) / 2)

    # Forward Moving Average
    for i in np.arange(k, len(signal) - k):
        for ii in np.arange(i - k, i + k + 1):
            sum = sum + signal[ii]
        mAver_forward.append(sum / window)
        sum = 0

    zeros = [0] * k
    mAver_forward = zeros + mAver_forward + zeros

    # Backward Moving Average
    signal = mAver_forward[::-1]
    for i in np.arange(k, len(signal) - k):
        for ii in np.arange(i - k, i + k + 1):
            sum = sum + signal[ii]
        mAver_backward.append(sum / window)
        sum = 0

    mAver_backward = mAver_backward[::-1]
    zeros = [0] * k
    mAver_backward = zeros + mAver_backward + zeros

    return mAver_backward


signal = movingAverage(signal, 20)

fig_mav_preprocess = go.Figure()
fig_mav_preprocess.add_trace(go.Scatter(x=time, y=signal, mode='lines', name="Signal SQRT"))
fig_mav_preprocess.update_layout(
    title="Original Signal",
    xaxis_title="Sequence (n)",
    yaxis_title="Amplitude (mV)",
    width=800,
    height=500,
    xaxis=dict(showline=True, showgrid=True),
    yaxis=dict(showline=True, showgrid=True)
)
# Show the plot
fig_mav_preprocess.show()

In [6]:
#Memasukan dataset sinyal p ke dalam variabel
signal_P=[]
for i in range(N):
    if i>=1300 and i<=1550:
        signal_P.append(signal[i])
    else:
        signal_P.append(0)

signal_QRS=[]
for i in range(N):
    if i>=1550 and i<=1680:
        signal_QRS.append(signal[i])
    else:
        signal_QRS.append(0)

signal_T=[]
for i in range(N):
    if i>=1680 and i<=2000:
        signal_T.append(signal[i])
    else:
        signal_T.append(0)

fig_segmentation = go.Figure()

fig_segmentation.add_trace(go.Scatter(x=time, y=signal_P, mode='lines', name="Signal P"))
fig_segmentation.add_trace(go.Scatter(x=time, y=signal_QRS, mode='lines', name="Signal QRS"))
fig_segmentation.add_trace(go.Scatter(x=time, y=signal_T, mode='lines', name="Signal T"))

fig_segmentation.update_layout(
    title="Segmented Signals",
    xaxis_title="Sequence (n)",
    yaxis_title="Amplitude (mV)",
    width=800,
    height=500,
    xaxis=dict(showline=True, showgrid=True),
    yaxis=dict(showline=True, showgrid=True)
)

fig_segmentation.show()

In [7]:
MagDFT_P = discrete_forrier_transform(N, fs, signal_P)
MagDFT_QRS = discrete_forrier_transform(N, fs, signal_QRS)
MagDFT_T = discrete_forrier_transform(N, fs, signal_T)
k =  np.arange (0, N, 1, dtype=int)
n = np.arange (0, N, 1, dtype=int)

#Plotting 
fig_DFT_Segmentation = go.Figure()
fig_DFT_Segmentation.add_trace(go.Scatter(x=k*fs/N, y=MagDFT_P, mode='lines', name="DFT Signal P"))
fig_DFT_Segmentation.add_trace(go.Scatter(x=k*fs/N, y=MagDFT_QRS, mode='lines', name="DFT Signal QRS"))
fig_DFT_Segmentation.add_trace(go.Scatter(x=k*fs/N, y=MagDFT_T, mode='lines', name="DFT Signal T"))
fig_DFT_Segmentation.update_layout(
    title="DFT Signal",
    xaxis_title="Frequency (Hz)",
    yaxis_title="Magnitude)",
    width=800,
    height=500,
    xaxis=dict(showline=True, showgrid=True),
    yaxis=dict(showline=True, showgrid=True)
)
fig_DFT_Segmentation.show()

In [8]:
import math
def butterworth_lowpass_filter(signal, cutoff_frequency, sampling_period, orde):
    y = np.zeros(len(signal)) 
    omega_c = 2 * np.pi * cutoff_frequency
    omega_c_squared = omega_c*omega_c
    sampling_period_squared = sampling_period*sampling_period
    if orde == 1:
        for n in range(len(signal)):
            if n == 0:
                y[n] = (omega_c * signal[n]) / ((2 / sampling_period) + omega_c)
            else:
                y[n] = (((2 / sampling_period) - omega_c) * y[n-1] + omega_c * signal[n] + omega_c * signal[n-1]) / ((2 / sampling_period) + omega_c)
    elif orde == 2:
        y[0] = (omega_c * signal[0]) / ((2 / sampling_period) + omega_c)
        y[1] = (((2 / sampling_period) - omega_c) * y[0] + omega_c * signal[1] + omega_c * signal[0]) / ((2 / sampling_period) + omega_c)
        for n in range(2, len(signal)):
            y[n] = (((8/sampling_period_squared)-2*omega_c_squared) * y[n-1]
                - ((4/sampling_period_squared) - (2 * np.sqrt(2) * omega_c / sampling_period) + omega_c_squared) * y[n-2]
                + omega_c_squared * signal[n]
                + 2 * omega_c_squared * signal[n-1]
                + omega_c_squared * signal[n-2]) / ((4/sampling_period_squared) + (2 * np.sqrt(2) * omega_c / sampling_period) + omega_c_squared)

    return y
# Define the cutoff frequency
cutoff_frequency = 12
sampling_period = 1/fs
# Apply the Butterworth filter
filtered_signal = butterworth_lowpass_filter(signal, cutoff_frequency, sampling_period, 1)

# Create a Plotly figure
fig_LPF = go.Figure()
fig_LPF.add_trace(go.Scatter(x=time, y=signal, mode='lines', name="After LPF"))
fig_LPF.add_trace(go.Scatter(x=time, y=filtered_signal, mode='lines', name="After LPF"))
fig_LPF.update_layout(
    title="Original Signal",
    xaxis_title="Sequence (n)",
    yaxis_title="Amplitude (mV)",
    width=800,
    height=500,
    xaxis=dict(showline=True, showgrid=True),
    yaxis=dict(showline=True, showgrid=True)
)
# Show the plot
fig_LPF.show()

In [9]:
import math
def butterworth_highpass_filter(signal, cutoff_frequency, sampling_period, orde):
    y = np.zeros(len(signal))  # Initialize the output signal
    omega_c = 2 * np.pi * cutoff_frequency
    omega_c_squared = omega_c*omega_c
    sampling_period_squared = sampling_period*sampling_period

    if orde == 1:
        for n in range(len(signal)):
            if n == 0:
                y[n] = (omega_c * signal[n]) / ((2 / sampling_period) + omega_c)
            else:
                y[n] = (((2 / sampling_period) - omega_c) * y[n-1] + (2 / sampling_period) * signal[n] + (2 / sampling_period) * signal[n-1]) / ((2 / sampling_period) + omega_c)

    elif orde == 2:
        y[0] = (omega_c * signal[0]) / ((2 / sampling_period) + omega_c)
        y[1] = (((2 / sampling_period) - omega_c) * y[0] + (2 / sampling_period) * signal[1] + (2 / sampling_period) * signal[0]) / ((2 / sampling_period) + omega_c)

        for n in range(2, (len(signal))):
            y[n] = ((4/sampling_period_squared)*signal[n] - (8/sampling_period_squared)*signal[n-1] + (4/sampling_period_squared)*signal[n-2] - (2*omega_c-(8/sampling_period_squared))*y[n-1] - (omega_c-(2*math.sqrt(2)*omega_c/sampling_period)+(4/sampling_period_squared))*y[n-2])/(omega_c + 2*math.sqrt(2)*omega_c/sampling_period + (4/sampling_period_squared))    
    return y

# Define the cutoff frequency
cutoff_frequency = 12
sampling_period = 1/fs
# Apply the Butterworth filter
filtered_signal_hpf = butterworth_highpass_filter(filtered_signal, cutoff_frequency, sampling_period, 2)

# Create a Plotly figure
fig_HPF = go.Figure()
fig_HPF.add_trace(go.Scatter(x=time, y=filtered_signal, mode='lines', name="After LPF"))
fig_HPF.add_trace(go.Scatter(x=time, y=filtered_signal_hpf, mode='lines', name="After HPF"))
fig_HPF.update_layout(
    title="Original Signal",
    xaxis_title="Sequence (n)",
    yaxis_title="Amplitude (mV)",
    width=800,
    height=500,
    xaxis=dict(showline=True, showgrid=True),
    yaxis=dict(showline=True, showgrid=True)
)
# Show the plot
fig_HPF.show()

In [10]:
signal_sqrt = []
for i in range (len(signal)):
    signal_sqrt.append(filtered_signal_hpf[i]*filtered_signal_hpf[i])

signal_mav = movingAverage(signal_sqrt, 20)

fig_mav = go.Figure()
fig_mav.add_trace(go.Scatter(x=time, y=signal_sqrt, mode='lines', name="Signal SQRT"))
fig_mav.add_trace(go.Scatter(x=time, y=signal_mav, mode='lines', name="Signal MAV"))
fig_mav.update_layout(
    title="Original Signal",
    xaxis_title="Sequence (n)",
    yaxis_title="Amplitude (mV)",
    width=800,
    height=500,
    xaxis=dict(showline=True, showgrid=True),
    yaxis=dict(showline=True, showgrid=True)
)
# Show the plot
fig_mav.show()

In [11]:
signal_threshold = []
for i in range (N):
    if signal_mav[i]>0.15 * np.max(signal_mav):
        signal_threshold.append(np.max(filtered_signal))
    else:
        signal_threshold.append(0)

fig_threshold = go.Figure()
fig_threshold.add_trace(go.Scatter(x=time, y=filtered_signal, mode='lines', name="Filtered Signal"))
fig_threshold.add_trace(go.Scatter(x=time, y=signal_threshold, mode='lines', name="Signal Threshold"))
fig_threshold.update_layout(
    title="Original Signal",
    xaxis_title="Sequence (n)",
    yaxis_title="Amplitude (mV)",
    width=800,
    height=500,
    xaxis=dict(showline=True, showgrid=True),
    yaxis=dict(showline=True, showgrid=True)
)
fig_threshold.show()

In [12]:
import pandas as pd
# Hitung jumlah puncak dalam signal_threshold
def count_peaks_qrs_width(signal, signal_threshold):
    peaks = 0
    for i in range(0, len(signal_threshold) - 1):
        if signal_threshold[i] > signal_threshold[i - 1]:
            peaks += 1
        elif signal_threshold[i] == signal_threshold[i-1]:
            continue

    #print("ECG Cycle:", peaks, "beats in", len(signal)/fs, "second")

    durasi_dalam_menit = (len(signal)/fs) / 60
    # count bpm
    bpm = peaks / durasi_dalam_menit
    #print("BPM (Beats Per Minute):", bpm)

    # Count QRS Width 
    qrs_widths = []
    j = 0
    p=0
    i=0
    while (i<len(signal)):
        if signal_threshold[i] != 0:
            while (i < (len(signal_threshold) - 1)) and signal_threshold[i + 1] != 0:
                j += 1
                i += 1
            qrs_widths.append(j)
        j = 0
        i+=1

    avarage_qrs_widths= 0
    for i in range(len(qrs_widths)):
        avarage_qrs_widths+= qrs_widths[i]

    avarage_qrs_widths = (avarage_qrs_widths/(len(qrs_widths)))/fs
    return peaks, bpm, qrs_widths, avarage_qrs_widths

peaks, bpm, qrs_widths, avarage_qrs_widths = count_peaks_qrs_width(signal, signal_threshold)

print(f"Jumlah peak dalam dataset :{peaks} peak")
print(f"Heart Rate                : {bpm} beat per minute")
print("QRS Width")
qrs_widths_df = pd.DataFrame({'QRS_Widths': qrs_widths})
print(qrs_widths_df)
print(f"Avarage QRS {avarage_qrs_widths}")

Jumlah peak dalam dataset :7 peak
Heart Rate                : 84.0 beat per minute
QRS Width
   QRS_Widths
0          68
1          69
2          69
3          70
4          70
5          71
6          69
Avarage QRS 0.06942857142857144


In [13]:
#DFT Signal After Filtering LPF

MagDFT_Filtered_LPF = discrete_forrier_transform(N, fs, filtered_signal)
k =  np.arange (0, N, 1, dtype=int)
n = np.arange (0, N, 1, dtype=int)

#Plotting 
fig_DFT_Filtered_LPF = go.Figure()
fig_DFT_Filtered_LPF.add_trace(go.Scatter(x=k*fs/N, y=MagDFT_Filtered_LPF, mode='lines', name="DFT Signal P"))
fig_DFT_Filtered_LPF.update_layout(
    title="DFT Signal",
    xaxis_title="Frequency (Hz)",
    yaxis_title="Magnitude)",
    width=800,
    height=500,
    xaxis=dict(showline=True, showgrid=True),
    yaxis=dict(showline=True, showgrid=True)
)
fig_DFT_Filtered_LPF.show()

In [14]:
import plotly.graph_objects as go

def create_plotly_figure(title, xaxis, yaxis, time, signal, name, mode):
    # Create a Plotly figure
    fig = go.Figure()

    for i in range(len(signal)):
        fig.add_trace(go.Scatter(x=time, y=signal[i], mode=mode, name=name[i]))

    # Update layout
    fig.update_layout(
        title=title,
        xaxis_title=xaxis,
        yaxis_title=yaxis,
        width=800,
        height=500,
        xaxis=dict(showline=True, showgrid=True),
        yaxis=dict(showline=True, showgrid=True)
    )

    fig.show()


create_plotly_figure('Signal Processing Results','Sequence (n)','Amplitude (mV)',time, [signal, filtered_signal], ['Original Signal', 'Filtered Signal'],'lines')
